In [ ]:
!pip install snowflake-snowpark-python

In [ ]:
!nvidia-smi

Wed Apr 24 03:13:16 2024       
+---------------------------------------------------------------------------------------+
| NVIDIA-SMI 535.104.05             Driver Version: 535.104.05   CUDA Version: 12.2     |
|-----------------------------------------+----------------------+----------------------+
| GPU  Name                 Persistence-M | Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp   Perf          Pwr:Usage/Cap |         Memory-Usage | GPU-Util  Compute M. |
|                                         |                      |               MIG M. |
|=========================================+======================+======================|
|   0  Tesla T4                       Off | 00000000:00:04.0 Off |                    0 |
| N/A   43C    P8              11W /  70W |      0MiB / 15360MiB |      0%      Default |
|                                         |                      |                  N/A |
+-----------------------------------------+----------------------+--

In [ ]:
import configparser
import sys
import os
from snowflake.snowpark import Session
import matplotlib.pyplot as plt
import pandas as pd
import numpy as np
from snowflake.snowpark.functions import col, sproc,udf
from snowflake.snowpark.types import StringType, Variant, ArrayType
import seaborn as sns
import snowflake


In [ ]:
def makeSnowflakeConnection(connection_name):
    global config
    config = configparser.RawConfigParser()
    config.read('/content/configConnection.properties')
    warehouse = config.get(connection_name, 'warehouse')
    user = config.get(connection_name, 'user')
    password =config.get(connection_name, 'password')
    account=config.get(connection_name, 'account')
    role=config.get(connection_name, 'role')
    conn = dict(
                user=user,
                password=password,
                account=account,
                warehouse=warehouse,
                role=role
                )
    session = Session.builder.configs(conn).create()
    return session
session=makeSnowflakeConnection('DBMS_PROJECT')

In [ ]:
session.use_database('COVID19_TRIAL')
session.use_schema('TRANSFORMED_DATA')

In [ ]:
df_tweets2=session.table("TWEETS_TRANSLATED").to_pandas()
df_retweets2=session.table("RETWEETS_TRANSLATED").to_pandas()

In [ ]:
import pandas as pd
from transformers import pipeline
import numpy as np

# Initialize the sentiment analysis pipeline with the RoBERTa model configured to use GPU
sentiment_analysis = pipeline("sentiment-analysis", model="cardiffnlp/twitter-roberta-base-sentiment", device=0)  # device=0 for the first GPU

def analyze_sentiment(batch):
    # Process the batch of texts, ensuring each entry is a string and not empty
    processed_texts = [text for text in batch if isinstance(text, str) and text.strip()]
    # Perform sentiment analysis and extract labels
    results = sentiment_analysis(processed_texts)
    return [result['label'] for result in results]

# Example DataFrame setup
# Define batch size based on your GPU memory capability
batch_size = 32  # Adjust as necessary

# Split the DataFrame into batches
batches = [df_tweets2['translated_text'][i:i + batch_size] for i in range(0, len(df_tweets2), batch_size)]

# Analyze sentiment for each batch and concatenate results
df_tweets2['sentiment'] = pd.concat([pd.Series(analyze_sentiment(batch)) for batch in batches], ignore_index=True)

print(df_tweets2)


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


config.json:   0%|          | 0.00/747 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/499M [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/899k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/456k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/150 [00:00<?, ?B/s]

You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset


                           CREATED_AT                   ID  \
0      Sun Apr 12 18:27:26 +0000 2020  1249403771261722624   
1      Sun Apr 12 18:27:29 +0000 2020  1249403785010491392   
2      Sun Apr 12 18:27:31 +0000 2020  1249403790098341894   
3      Sun Apr 12 18:27:32 +0000 2020  1249403794258972672   
4      Sun Apr 12 18:27:32 +0000 2020  1249403795643043840   
...                               ...                  ...   
48137  Sat Apr 25 14:48:33 +0000 2020  1254059727987912710   
48138  Sat Apr 25 14:48:34 +0000 2020  1254059733889232897   
48139  Sat Apr 25 14:48:35 +0000 2020  1254059739153137664   
48140  Sat Apr 25 14:48:36 +0000 2020  1254059742856728580   
48141  Sat Apr 25 14:48:38 +0000 2020  1254059749055889409   

                                                    TEXT  \
0      #Bo der Osterhase hat nicht Corona, er ist gek...   
1      We’r all going thru a difficult time due to Co...   
2      I really hate for people to sneeze and cough w...   
3              

In [ ]:
label_map = {
    'LABEL_0': 'Negative',
    'LABEL_1': 'Neutral',
    'LABEL_2': 'Positive'
}

# Map the sentiment labels to human-readable form
df_tweets2['sentiment'] = df_tweets2['sentiment'].map(label_map)

In [ ]:
df_tweets2['sentiment']

0         Neutral
1         Neutral
2        Negative
3         Neutral
4         Neutral
           ...   
48137    Negative
48138    Negative
48139    Negative
48140    Positive
48141     Neutral
Name: sentiment, Length: 48142, dtype: object

In [ ]:
import pandas as pd
from transformers import pipeline

# Initialize the emotion recognition pipeline with the model, configured to use GPU (device=0)
emotion_recognition = pipeline("text-classification", model="bhadresh-savani/distilbert-base-uncased-emotion", device=0)

def analyze_emotion(batch):
    # Process the batch of texts, ensure each entry is a string and not empty
    processed_texts = [text for text in batch if isinstance(text, str) and text.strip()]
    # Perform emotion recognition and extract labels
    results = emotion_recognition(processed_texts)
    return [result['label'] for result in results]

# Example DataFrame setup (assuming 'translated_text' contains textual data)


# Define batch size based on your GPU memory capability
batch_size = 32  # Adjust as necessary

# Split the DataFrame into batches
batches = [df_tweets2['translated_text'][i:i + batch_size] for i in range(0, len(df_tweets2), batch_size)]

# Analyze emotion for each batch and concatenate results
df_tweets2['emotion'] = pd.concat([pd.Series(analyze_emotion(batch)) for batch in batches], ignore_index=True)


print(df_tweets2)


config.json:   0%|          | 0.00/768 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/268M [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/291 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

                           CREATED_AT                   ID  \
0      Sun Apr 12 18:27:26 +0000 2020  1249403771261722624   
1      Sun Apr 12 18:27:29 +0000 2020  1249403785010491392   
2      Sun Apr 12 18:27:31 +0000 2020  1249403790098341894   
3      Sun Apr 12 18:27:32 +0000 2020  1249403794258972672   
4      Sun Apr 12 18:27:32 +0000 2020  1249403795643043840   
...                               ...                  ...   
48137  Sat Apr 25 14:48:33 +0000 2020  1254059727987912710   
48138  Sat Apr 25 14:48:34 +0000 2020  1254059733889232897   
48139  Sat Apr 25 14:48:35 +0000 2020  1254059739153137664   
48140  Sat Apr 25 14:48:36 +0000 2020  1254059742856728580   
48141  Sat Apr 25 14:48:38 +0000 2020  1254059749055889409   

                                                    TEXT  \
0      #Bo der Osterhase hat nicht Corona, er ist gek...   
1      We’r all going thru a difficult time due to Co...   
2      I really hate for people to sneeze and cough w...   
3              

In [ ]:
import pandas as pd
from transformers import pipeline
import numpy as np

# Initialize the sentiment analysis pipeline with the RoBERTa model configured to use GPU
sentiment_analysis = pipeline("sentiment-analysis", model="cardiffnlp/twitter-roberta-base-sentiment", device=0)  # device=0 for the first GPU

def analyze_sentiment(batch):
    # Process the batch of texts, ensuring each entry is a string and not empty
    processed_texts = [text for text in batch if isinstance(text, str) and text.strip()]
    # Perform sentiment analysis and extract labels
    results = sentiment_analysis(processed_texts)
    return [result['label'] for result in results]

# Example DataFrame setup
# Define batch size based on your GPU memory capability
batch_size = 32  # Adjust as necessary

# Split the DataFrame into batches
batches = [df_retweets2['translated_text'][i:i + batch_size] for i in range(0, len(df_retweets2), batch_size)]

# Analyze sentiment for each batch and concatenate results
df_retweets2['sentiment'] = pd.concat([pd.Series(analyze_sentiment(batch)) for batch in batches], ignore_index=True)
label_map = {
    'LABEL_0': 'Negative',
    'LABEL_1': 'Neutral',
    'LABEL_2': 'Positive'
}

# Map the sentiment labels to human-readable form
df_retweets2['sentiment'] = df_retweets2['sentiment'].map(label_map)
print(df_retweets2)


                           CREATED_AT                   ID  \
0      Sat Apr 25 13:11:54 +0000 2020  1254035405218832384   
1      Sat Apr 25 13:11:54 +0000 2020  1254035408108900353   
2      Sat Apr 25 13:11:56 +0000 2020  1254035414907785217   
3      Sat Apr 25 13:11:58 +0000 2020  1254035422885412871   
4      Sat Apr 25 13:11:58 +0000 2020  1254035424961597440   
...                               ...                  ...   
72253  Sat Apr 25 13:11:47 +0000 2020  1254035379533107200   
72254  Sat Apr 25 13:11:50 +0000 2020  1254035388005400577   
72255  Sat Apr 25 13:11:51 +0000 2020  1254035394506764289   
72256  Sat Apr 25 13:11:52 +0000 2020  1254035397132218368   
72257  Sat Apr 25 13:11:52 +0000 2020  1254035399737061376   

                                                    TEXT  \
0      RT @drvinash: Excellent contribution during lo...   
1      RT @Quirinale: #25Aprile, il Presidente #Matta...   
2      RT @CesareSacchetti: Un 40enne ha tentato il s...   
3      RT @EdGa

In [ ]:
import pandas as pd
from transformers import pipeline

# Initialize the emotion recognition pipeline with the model, configured to use GPU (device=0)
emotion_recognition = pipeline("text-classification", model="bhadresh-savani/distilbert-base-uncased-emotion", device=0)

def analyze_emotion(batch):
    # Process the batch of texts, ensure each entry is a string and not empty
    processed_texts = [text for text in batch if isinstance(text, str) and text.strip()]
    # Perform emotion recognition and extract labels
    results = emotion_recognition(processed_texts)
    return [result['label'] for result in results]

# Example DataFrame setup (assuming 'translated_text' contains textual data)


# Define batch size based on your GPU memory capability
batch_size = 32  # Adjust as necessary

# Split the DataFrame into batches
batches = [df_retweets2['translated_text'][i:i + batch_size] for i in range(0, len(df_retweets2), batch_size)]

# Analyze emotion for each batch and concatenate results
df_retweets2['emotion'] = pd.concat([pd.Series(analyze_emotion(batch)) for batch in batches], ignore_index=True)


print(df_retweets2)


                           CREATED_AT                   ID  \
0      Sat Apr 25 13:11:54 +0000 2020  1254035405218832384   
1      Sat Apr 25 13:11:54 +0000 2020  1254035408108900353   
2      Sat Apr 25 13:11:56 +0000 2020  1254035414907785217   
3      Sat Apr 25 13:11:58 +0000 2020  1254035422885412871   
4      Sat Apr 25 13:11:58 +0000 2020  1254035424961597440   
...                               ...                  ...   
72253  Sat Apr 25 13:11:47 +0000 2020  1254035379533107200   
72254  Sat Apr 25 13:11:50 +0000 2020  1254035388005400577   
72255  Sat Apr 25 13:11:51 +0000 2020  1254035394506764289   
72256  Sat Apr 25 13:11:52 +0000 2020  1254035397132218368   
72257  Sat Apr 25 13:11:52 +0000 2020  1254035399737061376   

                                                    TEXT  \
0      RT @drvinash: Excellent contribution during lo...   
1      RT @Quirinale: #25Aprile, il Presidente #Matta...   
2      RT @CesareSacchetti: Un 40enne ha tentato il s...   
3      RT @EdGa

In [ ]:
session.write_pandas(df_tweets2, 'TWEETS_EMOSEN',auto_create_table=True).collect()

[Row(CREATED_AT='Sun Apr 12 18:27:26 +0000 2020', ID='1249403771261722624', TEXT='#Bo der Osterhase hat nicht Corona, er ist gekommen.', SOURCE='<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>', TRUNCATED=False, IN_REPLY_TO_STATUS_ID=None, IN_REPLY_TO_USER_ID=None, IN_REPLY_TO_SCREEN_NAME=None, USER_ID='1171484224244744198', USER_NAME='Elfpunkt', USER_SCREEN_NAME='meElfpunkt', USER_LOCATION=None, USER_DESCRIPTION='Mal 1 mal 0 mal Tilt', USER_PROTECTED=False, USER_FOLLOWERS_COUNT=3, USER_FRIENDS_COUNT=53, USER_LISTED_COUNT=0, USER_FAVOURITES_COUNT=72, USER_STATUSES_COUNT=60, USER_CREATED_AT='Tue Sep 10 18:03:17 +0000 2019', USER_GEO_ENABLED=False, GEO=None, COORDINATES=None, PLACE=None, IS_QUOTE_STATUS=False, QUOTE_COUNT=0, REPLY_COUNT=0, RETWEET_COUNT=0, FAVORITE_COUNT=0, ENTITIES_HASHTAGS='[\n  {\n    "indices": [\n      0,\n      3\n    ],\n    "text": "Bo"\n  }\n]', ENTITIES_SYMBOLS='[]', ENTITIES_USER_MENTIONS='[]', ENTITIES_URLS='[]', LANG='de'

In [ ]:
session.write_pandas(df_retweets2, 'RETWEETS_EMOSEN',auto_create_table=True).collect()

[Row(CREATED_AT='Sat Apr 25 14:28:15 +0000 2020', ID='1254054620806201344', TEXT='RT @profwolff: "Re-open the economy" when US Corona deaths doubled in last week? \n\nYes, that happens when "stable geniuses" see re-election…', SOURCE='<a href="http://twitter.com/download/android" rel="nofollow">Twitter for Android</a>', TRUNCATED=False, USER_ID='1228259402974666753', USER_NAME='🎩DominiqueRodrigue🎩☆ProudSatanist⚔Ave👁Satanas☆', USER_SCREEN_NAME='GirluniqueXOXOX', USER_LOCATION='USA⚖4ever27yrs🦇AnimalRights🌹', USER_DESCRIPTION='FrenchProgressiveSecularDemocraticSocialist🕸Into-Goth🕷Math&Science🖤BlackMetal🕷Comics🖤Horrour🕷\nPolitics~AntiRepublican☠AntiCorporateDemocrat🕸🔥LuvBernie🔥', USER_PROTECTED=False, USER_FOLLOWERS_COUNT=744, USER_FRIENDS_COUNT=2450, USER_LISTED_COUNT=0, USER_FAVOURITES_COUNT=17521, USER_STATUSES_COUNT=25055, USER_CREATED_AT='Fri Feb 14 10:07:55 +0000 2020', USER_GEO_ENABLED=True, IS_QUOTE_STATUS=False, QUOTE_COUNT=0, REPLY_COUNT=0, RETWEET_COUNT=0, FAVORITE_COUNT=0, ENTI